In [1]:
import napari
import os
from tqdm import tqdm
import numpy as np
import glob2 as glob
import zarr
import json
import skimage.io as io
import pandas as pd
import umap.umap_ as umap
from sklearn.preprocessing import StandardScaler

# # set parameters
root = "E:\\Nick\\Cole Trapnell's Lab Dropbox\\Nick Lammers\\Nick\\killi_tracker\\"
project_name = "240219_LCP1_93hpf_to_127hpf"
image_dir = os.path.join(root, "built_data", project_name, "")
config_name = "tracking_v1.txt"
tracking_folder = config_name.replace(".txt", "")
tracking_folder = tracking_folder.replace(".toml", "")

tracking_directory = os.path.join(root, "built_data", "tracking", project_name, tracking_folder)
snip_directory = os.path.join(root, "built_data", "shape_snips", project_name, tracking_folder, "class0")

# load metadata
metadata_file_path = os.path.join(root, "metadata", project_name, "metadata.json")
f = open(metadata_file_path)
metadata = json.load(f)
scale_vec = np.asarray([metadata["ProbPhysicalSizeZ"], metadata["ProbPhysicalSizeY"], metadata["ProbPhysicalSizeX"]])

In [2]:
tracks_df = pd.read_csv(os.path.join(tracking_directory, "tracks.csv"))
tracks_df.head()

In [82]:
from tqdm import tqdm
dt = 90

window_size_vec = [5, 25]

for window_size in window_size_vec:
    w_str = str(window_size)
    c_time = dt*(window_size-1)
    buffer_size = window_size // 2
    track_index = np.unique(tracks_df["track_id"])

    for t, track_id in enumerate(tqdm(track_index)):
        track_bool = tracks_df["track_id"] == track_id

        if np.sum(track_bool) >= window_size:
            xyz = tracks_df.loc[track_bool, ["x", "y", "z"]].to_numpy()

            # get contour length
            d1 = np.sqrt(np.sum(np.diff(xyz, 1, axis=0)**2, axis=1))
            d1_cs = np.cumsum(d1)
            cs1 = d1_cs[window_size-2:]
            cs2 = np.concatenate(([0], d1_cs[:-window_size+1]))
            contour_r = cs1 - cs2

            # get net displacement
            net_r = np.sqrt(np.sum((xyz[window_size-1:, :] - xyz[:-window_size+1, :])**2, axis=1))

            # assign to tracks df
            to_indices = np.where(track_bool)[0]
            to_indices = to_indices[buffer_size:-buffer_size]
            tracks_df.loc[to_indices, "speed_" + w_str] = contour_r / c_time
            tracks_df.loc[to_indices, "speed_net_" + w_str] = net_r / c_time
            tracks_df.loc[to_indices, "coherence_" + w_str] = net_r / contour_r


        

  0%|          | 0/331 [00:00<?, ?it/s]C:\Users\nlammers\AppData\Local\Temp\ipykernel_28988\3890418612.py:33: RuntimeWarning:

invalid value encountered in divide

 20%|█▉        | 66/331 [00:00<00:00, 647.06it/s]C:\Users\nlammers\AppData\Local\Temp\ipykernel_28988\3890418612.py:33: RuntimeWarning:

invalid value encountered in divide

C:\Users\nlammers\AppData\Local\Temp\ipykernel_28988\3890418612.py:33: RuntimeWarning:

invalid value encountered in divide

 41%|████      | 136/331 [00:00<00:00, 670.13it/s]C:\Users\nlammers\AppData\Local\Temp\ipykernel_28988\3890418612.py:33: RuntimeWarning:

invalid value encountered in divide

C:\Users\nlammers\AppData\Local\Temp\ipykernel_28988\3890418612.py:33: RuntimeWarning:

invalid value encountered in divide

C:\Users\nlammers\AppData\Local\Temp\ipykernel_28988\3890418612.py:33: RuntimeWarning:

invalid value encountered in divide

 65%|██████▌   | 216/331 [00:00<00:00, 725.51it/s]C:\Users\nlammers\AppData\Local\Temp\ipykernel_28988\389041861

In [81]:
import plotly.express as px
t_vec = tracks_df["t"].to_numpy()
c_vec = tracks_df["coherence"].to_numpy()

nn_vec = (~np.isnan(t_vec)) & (~np.isnan(c_vec))

dyn_hist, xe, ye = np.histogram2d(c_vec[nn_vec], t_vec[nn_vec], bins=[20, 20])
dyn_hist = np.divide(dyn_hist, np.sum(dyn_hist, axis=0))

track_id = 1
fig = px.imshow(np.flipud(dyn_hist))
fig.show()
                     
# fig = px.density_contour(tracks_df, x="t", y="coherence")
# fig.update_traces(contours_coloring="fill", contours_showlabels = True)
# fig.show()

In [84]:
fig = px.scatter(tracks_df, x="t", y="coherence_25", color="t")
fig.show()

In [98]:
fig = px.density_contour(tracks_df, x="t", y="speed_5")
fig.update_traces(contours_coloring="fill", contours_showlabels = True, colorscale="Blues")
fig.show()

In [88]:
shape_df = pd.read_csv(os.path.join(tracking_directory, "cell_shape_df.csv"))
shape_df.head()

track_id  t  complexity  area  solidity  eccentricity  circularity
0         1  0    1.074967  64.0  0.914286      1.834204     0.526947
1         1  1    1.107726  67.0  0.930556      1.873470     0.511322
2         1  2    1.219162  74.0  0.850575      2.050304     0.444854
3         1  3    1.145817  81.0  0.880435      2.152514     0.437290
4         1  4    1.159344  70.0  0.897436      2.045594     0.446407

In [96]:
fig = px.density_contour(shape_df, x="t", y="circularity")
fig.update_traces(contours_coloring="fill", contours_showlabels = True, colorscale="Blues")
fig.show()

In [99]:
master_df = tracks_df.merge(shape_df, on=["track_id", "t"], how="left")

In [109]:
master_df["time_id"] = np.floor(master_df["t"].to_numpy()/350).astype(int)

fig = px.density_contour(master_df, x="eccentricity", y="speed_25", color="time_id")
# fig.update_traces(contours_coloring="fill", contours_showlabels = True, colorscale="Blues")
fig.show()

In [106]:
np.unique(master_df["time_id"])

array(['[0 0 0 ... 5 5 5]'], dtype=object)